In [1]:
if True:
    import numpy as np
    import pandas as pd
    from scipy.optimize import curve_fit

    # Add lab library
    import sys
    sys.path.insert(0, '/home/trevormjs/Documents/Science/APL/Lab')

    #---------------------------------------------------------------------#
    #                        matplotlib plotting                          #
    #---------------------------------------------------------------------#
    import matplotlib.pyplot as plt
    import matplotlib as mpl
    from jupyterthemes import jtplot
    from Helper.plotting import my_graph
    # Edit the font, font size, and axes width
    # mpl.rcParams['font.family'] = 'Avenir'
    plt.rcParams['font.size'] = 24
    plt.rcParams['axes.linewidth'] = 2
    jtplot.style(theme='monokai', context='notebook', ticks=False, grid=False)

    #---------------------------------------------------------------------#
    #                           bokeh plotting                            #
    #---------------------------------------------------------------------#
    from bokeh.plotting import figure, show, output_notebook
    from bokeh.themes import Theme
    from bokeh.io import curdoc, export_png
    from bokeh.models import (Range1d, Label, ColumnDataSource, LabelSet,
                              Legend)
    from Helper.plotting import style
    output_notebook()
    # curdoc().theme = Theme(filename="../Helper/theme.yml")
    
    #---------------------------------------------------------------------#
    #                          plotly plotting                            #
    #---------------------------------------------------------------------#
    import plotly.express as ex

    #---------------------------------------------------------------------#
    #                       error and unit handling                       #
    #---------------------------------------------------------------------#
    from uncertainties import ufloat
    import Helper.numbers as nu
    from Helper.record import Measurement, Unit

    %load_ext autoreload
    %autoreload 2

Loading BokehJS ...

# Measure Inductance

In [2]:
def get_oscillation_start(data):
    on_end_ind = data.loc[data.mV > 5].index[-1]
    off_end_ind = data.loc[(data.mV < .5)
                           & (data.mV > 0)].index[-1]
    return data.loc[on_end_ind:off_end_ind]

## Data

In [3]:
# Inductances and uncertainties
R_A, R_B = 17.22, 17.41 # Ohms

In [4]:
[[A_circuit, A_circuit_config]] = nu.read_scope_csv('./Data/l6_A_A1.csv')

[[B_circuit, B_circuit_config]] = nu.read_scope_csv('./Data/l6_A_B1.csv')

{'record_length': [2500.0, 'Points'],
 'sample_interval': [2e-06, 's'],
 'trigger_point': [459.999982265, 'Samples']}

{'record_length': [2500.0, 'Points'],
 'sample_interval': [2e-06, 's'],
 'trigger_point': [520.000002728, 'Samples']}

In [5]:
[[A_circuit_short, A_circuit_short_config]] = nu.read_scope_csv('./Data/l6_A_A2.csv')

[[B_circuit_short, B_circuit_short_config]] = nu.read_scope_csv('./Data/l6_A_B2.csv')

{'record_length': [2500.0, 'Points'],
 'sample_interval': [4.0000000467e-07, 's'],
 'trigger_point': [-1700.0001, 'Samples']}

{'record_length': [2500.0, 'Points'],
 'sample_interval': [4.0000000467e-07, 's'],
 'trigger_point': [-2270.0, 'Samples']}

In [6]:
a = get_oscillation_start(A_circuit)
a.insert(0, 'AB', 'A')
b = get_oscillation_start(B_circuit)
b.insert(0, 'AB', 'B')
ab = pd.concat([a, b])
ab.index = range(ab.shape[0])

In [7]:
short_a = A_circuit_short.copy()
short_a.insert(0, 'AB', 'A')

short_b = B_circuit_short.copy()
short_b.insert(0, 'AB', 'B')

short = pd.concat([short_a, short_b])
short.index = range(short.shape[0])

## Plot

In [8]:
ex.line(short, 'ts','mV', color = 'AB')

In [9]:
ex.line(ab, 'ts','mV', color='AB')

## Fit

In [244]:

from bokeh.models import Label
from bokeh.util.compiler import TypeScript
TS_CODE = """
import * as p from "core/properties"
import {Label, LabelView} from "models/annotations/label"
declare const katex: any

export class LatexLabelView extends LabelView {
  model: LatexLabel

  render(): void {
    //--- Start of copied section from ``Label.render`` implementation

    // Here because AngleSpec does units tranform and label doesn't support specs
    let angle: number
    switch (this.model.angle_units) {
      case "rad": {
        angle = -this.model.angle
        break
      }
      case "deg": {
        angle = (-this.model.angle * Math.PI) / 180.0
        break
      }
      default:
        throw new Error("unreachable code")
    }

    const panel = this.layout ?? this.plot_view.layout.center_panel

    let sx = this.model.x_units == "data" ? this.coordinates.x_scale.compute(this.model.x) : panel.xview.compute(this.model.x)
    let sy = this.model.y_units == "data" ? this.coordinates.y_scale.compute(this.model.y) : panel.yview.compute(this.model.y)

    sx += this.model.x_offset
    sy -= this.model.y_offset

    //--- End of copied section from ``Label.render`` implementation
    // Must render as superpositioned div (not on canvas) so that KaTex
    // css can properly style the text
    this._css_text(this.layer.ctx, "", sx, sy, angle)

    // ``katex`` is loaded into the global window at runtime
    // katex.renderToString returns a html ``span`` element
    katex.render(this.model.text, this.el, {displayMode: true})
  }
}

export namespace LatexLabel {
  export type Attrs = p.AttrsOf<Props>

  export type Props = Label.Props
}

export interface LatexLabel extends LatexLabel.Attrs {}

export class LatexLabel extends Label {
  properties: LatexLabel.Props
  __view_type__: LatexLabelView

  constructor(attrs?: Partial<LatexLabel.Attrs>) {
    super(attrs)
  }

  static init_LatexLabel() {
    this.prototype.default_view = LatexLabelView
  }
}
"""

class LatexLabel(Label):
    """A subclass of the Bokeh built-in `Label` that supports rendering
    LaTex using the KaTex typesetting library.

    Only the render method of LabelView is overloaded to perform the
    text -> latex (via katex) conversion. Note: ``render_mode="canvas``
    isn't supported and certain DOM manipulation happens in the Label
    superclass implementation that requires explicitly setting
    `render_mode='css'`).
    """
    __javascript__ = ["https://cdnjs.cloudflare.com/ajax/libs/KaTeX/0.6.0/katex.min.js"]
    __css__ = ["https://cdnjs.cloudflare.com/ajax/libs/KaTeX/0.6.0/katex.min.css"]
    __implementation__ = TypeScript(TS_CODE)


In [259]:
def my_sine(x, a, b, c):
    return a*np.sin(b*x+c)

def my_exp(x, d):
    return np.exp(-d/2*x)

def sine_with_offset(x, a, b, c, offset): 
    return my_sine(x, a, b, c) + offset

def damped_oscillation_with_offset(x, a, b, c, d, offset):
    return my_sine(x, a, b, c) * my_exp(x, d) + offset

In [260]:
A_circuit_short = A_circuit_short.loc[(A_circuit_short.ts > 0.0009752) &
                                      (A_circuit_short.ts < 0.0014119)]

[a, b, c, offset], pcov = pop, pcov = curve_fit(
    sine_with_offset,
    A_circuit_short.ts,
    A_circuit_short.mV,
    maxfev=1000
)

while c < -2*np.pi:
    c += 2*np.pi
    pop[2] += 2*np.pi

A_circuit_short['fit'] = [
    sine_with_offset(x, *pop) for x in A_circuit_short.ts]

fig = figure(title = 'A_short fit', height = 400)
fig.scatter(A_circuit_short.ts*1e3, A_circuit_short.mV, color = 'red')
fig.line(A_circuit_short.ts*1e3, A_circuit_short.fit, color = 'black', line_width=3,
        legend_label = f"{pop[0]:.2f}cos({pop[1]:.0f}\cdot t + {pop[2]:.2f})")
style(fig)
fig.xaxis.axis_label = 't (ms)'
fig.y_range = Range1d( -3.2, 5)
show(fig)

In [261]:
fits = pd.DataFrame(index = ['A','$\omega$','$\phi$','$\gamma$','offset'])

In [262]:
A_circuit = get_oscillation_start(A_circuit)

[a, b, c, d, offset], pcov = pop, pcov = curve_fit(
    damped_oscillation_with_offset,
    A_circuit.ts,
    A_circuit.mV,
    maxfev=10000,
    p0=[0, b, c, 0, offset]
)

if 'fit' not in A_circuit.columns:
    A_circuit.insert(2, 'fit', [
        damped_oscillation_with_offset(x, *pop) for x in A_circuit.ts])
else:
    A_circuit['fit'] = [
        damped_oscillation_with_offset(x, *pop) for x in A_circuit.ts]
fits.insert(0, 'A', pop)

In [263]:
fig = figure(title = 'A fit', height = 400)
fig.scatter(A_circuit.ts*1e3, A_circuit.mV, color = 'red')
fig.line(A_circuit.ts*1e3, A_circuit.fit, color = 'black', line_width=3,
        legend_label = f"{pop[0]:.2f}cos({pop[1]:.0f}*t + {pop[2]:.2f}) exp(-{pop[3]:.0f}/2*x)")
style(fig)
fig.xaxis.axis_label = 't (ms)'
fig.y_range = Range1d( -5, 7.6)
style(fig)
show(fig)
export_png(fig, filename = '../Images/l6_A_3_A.png')

'/home/trevormjs/Documents/Science/APL/Lab/Images/l6_A_3_A.png'

In [264]:
B_circuit_short = B_circuit_short.loc[(B_circuit_short.ts > 0.0009752) &
                                      (B_circuit_short.ts < 0.0014119)]

([a, b, c, offset], pcov) = (pop, pcov) = curve_fit(
    sine_with_offset,
    B_circuit_short.ts,
    B_circuit_short.mV,
    maxfev=1000
)

while c > 2*np.pi:
    c -= 2*np.pi
    pop[2] -= 2*np.pi

B_circuit_short['fit'] = [
    sine_with_offset(x, *pop) for x in B_circuit_short.ts]

fig = figure(title = 'B_short fit', height = 400)
fig.scatter(B_circuit_short.ts*1e3, B_circuit_short.mV, color = 'red')
fig.line(B_circuit_short.ts*1e3, B_circuit_short.fit, color = 'black', line_width=3,
        legend_label = f"{pop[0]:.2f}cos({-pop[1]:.0f}*t + {pop[2]:.2f})".format('%f2'))
style(fig)
fig.xaxis.axis_label = 't (ms)'
fig.y_range = Range1d( -3.2, 5)
show(fig)

In [265]:
B_circuit = get_oscillation_start(B_circuit)

[a, b, c, d, offset], pcov = pop, pcov = curve_fit(
    damped_oscillation_with_offset,
    B_circuit.ts,
    B_circuit.mV,
    maxfev=10000,
    p0=[0, b, c, 0, offset]
)

if 'fit' not in B_circuit.columns:
    B_circuit.insert(2, 'fit', [
        damped_oscillation_with_offset(x, *pop) for x in B_circuit.ts])
else:
    B_circuit['fit'] = [
        damped_oscillation_with_offset(x, *pop) for x in B_circuit.ts]
fits.insert(0, 'B', pop)

In [274]:
np.abs(pcov[1]).mean()

0.0321363683415991

In [266]:
fig = figure(title = 'B fit', height = 400)
fig.scatter(B_circuit.ts*1e3, B_circuit.mV, color = 'red')
fig.line(B_circuit.ts*1e3, B_circuit.fit, color = 'black', line_width=3,
        legend_label = f"{pop[0]:.2f}cos({-pop[1]:.0f}*t + {pop[2]:.2f}) exp(-{pop[3]:.0f}/2*x)")
# style(fig)
fig.xaxis.axis_label = 't (ms)'
fig.y_range = Range1d( -5, 7.6)
style(fig)
show(fig)
export_png(fig, filename = '../Images/l6_A_3_B.png')

'/home/trevormjs/Documents/Science/APL/Lab/Images/l6_A_3_B.png'

In [267]:
C_standard = ufloat(47.23e-9, 5e-12)
fits.loc['$L$'] = 1/(fits.iloc[1,:]**2*C_standard)

In [268]:
fits

B                    A
A                    4.501309             4.466655
$\omega$        -14578.440019         14587.045275
$\phi$               3.286658             0.064953
$\gamma$           651.265721           649.911189
offset               0.199547             0.193248
$L$       0.099623+/-0.000011  0.099506+/-0.000011

In [ ]:
fits.axes[0].name = 'Parameter'

In [ ]:
fits.insert(0, 'Parameter', fits.index)

In [243]:
print(fits.drop('offset', 0).replace({'\textbackslash':'\\'}, ).to_latex(index=False))
fits

\begin{tabular}{lrr}
\toprule
Parameter &             B &             A \\
        A &      4.501309 &      4.466655 \\
\midrule
 \$\textbackslash omega\$ & -14578.440019 & -14587.045274 \\
   \$\textbackslash phi\$ &      3.286658 &      3.076640 \\
 \$\textbackslash gamma\$ &    651.265721 &    649.911186 \\
      NaN &      0.099623 &      0.099506 \\
\bottomrule
\end{tabular}



Parameter             B             A
Parameter                                      
A                 A      4.501309      4.466655
$\omega$   $\omega$ -14578.440019 -14587.045274
$\phi$       $\phi$      3.286658      3.076640
$\gamma$   $\gamma$    651.265721    649.911186
offset       offset      0.199547      0.193248
$L$             NaN      0.099623      0.099506

# Unilateral Excitation of Coupled Oscillators

In [44]:
[[coupled_A, coupled_config], [coupled_B, coupled_config]] = nu.read_scope_csv('./Data/l6_D_2.csv', 2)

{'record_length': [2500.0, 'Points'],
 'sample_interval': [9.999999747e-06, 's'],
 'trigger_point': [-1420.0001, 'Samples']}

{'record_length': [2500.0, 'Points'],
 'sample_interval': [9.999999747e-06, 's'],
 'trigger_point': [-1420.0001, 'Samples']}

In [46]:
fig = figure(width=1200)
fig.line(coupled_A.ts, coupled_A.mV+6, color = 'red', legend_label = 'A')
fig.line(coupled_A.ts, coupled_B.mV-6, color = 'blue', legend_label = 'B')
fig.line(coupled_A.ts, (coupled_B.mV+coupled_A.mV), color = 'purple', legend_label = 'Sum')
show(fig)

In [47]:
(coupled_A.mV)

0       5.12
1       5.12
2       5.04
3       4.88
4       4.64
        ... 
2043    0.16
2044    0.16
2045    0.16
2046    0.08
2047    0.16
Name: mV, Length: 2048, dtype: float64

In [52]:
coupled_sum = coupled_A.mV + coupled_B.mV
coupled_sum -= coupled_sum.mean()
fig = figure(width=1200)
[a, b, c, d, offset], pcov = pop, pcov = curve_fit(
    damped_oscillation_with_offset,
    coupled_A.ts,
    coupled_sum,
    maxfev=10000,
    p0=[0, b, c, 0, offset]
)
print(offset)
fit = np.array([damped_oscillation_with_offset(x, *pop) for x in coupled_A.ts])
fig = figure()
fig.scatter(coupled_A.ts, coupled_sum, color='red')
fig.line(coupled_A.ts, fit, color='black', line_width=3)
show(fig)

-0.0031337347615711855


In [63]:
from scipy.signal import hilbert

In [199]:
fig = figure(width=1200)
# fig.line(coupled_A.ts, nu.fft_filter((coupled_A.mV - coupled_A.mV.mean()), .09) /
#          np.exp(-d/2*coupled_A.ts), color='red', legend_label='A', line_width=3)
less_decay_B = nu.fft_filter(
    (coupled_B.mV - coupled_B.mV.mean()), .08) / np.exp(-d/2*coupled_A.ts)

fig.line(coupled_A.ts, less_decay_B, color='blue',
         legend_label='B', line_width=3)

peaks = np.concatenate([np.array([0]), nu.find_peaks(
    np.abs(less_decay_B[coupled_A.ts < .0322]))[0]])
fig.scatter(coupled_A.ts[peaks], np.abs(less_decay_B[peaks]), color='red', size=10)

[A, omega, phase, offset], pconv = curve_fit(
    sine_with_offset,
    coupled_A.ts[peaks],
    np.abs(less_decay_B[peaks]),
    p0=[100, 1000, 0, 100]
)

fig.line(coupled_A.ts, [abs(sine_with_offset(t, A, omega, phase, offset))
                        for t in coupled_A.ts], color='black')

fig.y_range = Range1d(-220, 220)
show(fig)

# fig.y_range = Range1d(-4, 4)
# fig.line(coupled_A.ts, (coupled_B.mV+coupled_A.mV), color = 'purple', legend_label = 'Sum')

In [200]:
coefs, freqs = nu.fft(less_decay_B[coupled_A.ts<.0322], coupled_A.ts[coupled_A.ts<.0322], 16)
fig = figure(width=700, height=300)
fig.line(freqs, coefs)
peak_inds, _ = nu.find_peaks(coefs)
peak_inds = peak_inds[coefs[peak_inds] > 30000]
peak_coefs = coefs[peak_inds]
peak_freqs = freqs[peak_inds]
fig.scatter(peak_freqs, peak_coefs)
fig.x_range = Range1d(1500, 3000)
show(fig)

omega_B_fit = omega/2/np.pi

omega_B_fft = peak_freqs[3]-peak_freqs[2]

omega_test_B = np.array([omega_B_fit, omega_B_fft])

u = nu.print_unc(omega_test.mean(), omega_test.std())

ts = coupled_A.ts
sine1 = np.cos(ts*peak_freqs[2]*2*np.pi)
sine2 = np.cos(ts*peak_freqs[3]*2*np.pi)
resultant = sine1+sine2
resultant = .5+np.sin(ts*(peak_freqs[3]-peak_freqs[2])*2*np.pi+2.45)/2
fig = figure(width=700, height=300)
# fig.line(ts, sine1, color = 'blue')
# fig.line(ts, sine2, color = 'red')
fig.line(ts, resultant, color = 'purple')
fig.line(coupled_A.ts, less_decay_B/less_decay_B.max())

show(fig)

167.8 +- 0.1


In [227]:
fig = figure(width=1200, height=300)
# fig.line(coupled_A.ts, nu.fft_filter((coupled_A.mV - coupled_A.mV.mean()), .09) /
#          np.exp(-d/2*coupled_A.ts), color='red', legend_label='A', line_width=3)
less_decay_A = nu.fft_filter(
    (coupled_A.mV - coupled_A.mV.mean()), .08) / np.exp(-d/2*coupled_A.ts)

fig.line(coupled_A.ts, less_decay_A, color='blue',
         legend_label='B', line_width=3)

peaks = nu.find_peaks(
    less_decay_A[coupled_A.ts < .029])[0]
fig.scatter(coupled_A.ts[peaks], less_decay_A[peaks], color='red', size=10)

[A, omega, phase, offset], pconv = curve_fit(
    sine_with_offset,
    coupled_A.ts[peaks],
    less_decay_A[peaks],
    p0=[100, 1000, 0, 100]
)

fig.line(coupled_A.ts, [sine_with_offset(t, A, omega, phase, offset)
                        for t in coupled_A.ts], color='black')

fig.y_range = Range1d(-220, 220)
show(fig)

# fig.y_range = Range1d(-4, 4)
# fig.line(coupled_A.ts, (coupled_B.mV+coupled_A.mV), color = 'purple', legend_label = 'Sum')

In [202]:
coefs, freqs = nu.fft(
    less_decay_A[coupled_A.ts < .029], coupled_A.ts[coupled_A.ts < .029], 16)
fig = figure(width=700, height=300)
fig.line(freqs, coefs)
peak_inds, _ = nu.find_peaks(coefs)
peak_inds = peak_inds[coefs[peak_inds] > 30000]
peak_coefs = coefs[peak_inds]
peak_freqs = freqs[peak_inds]
fig.scatter(peak_freqs, peak_coefs)
fig.x_range = Range1d(1500, 3000)
show(fig)

omega_A_fit = omega/2/np.pi

omega_A_fft = peak_freqs[3]-peak_freqs[2]

omega_test_A = np.array([omega_A_fit, omega_A_fft])
u = nu.print_unc(omega_test.mean(), omega_test.std())

ts = coupled_A.ts
sine1 = np.cos(ts*peak_freqs[2]*2*np.pi)
sine2 = np.cos(ts*peak_freqs[3]*2*np.pi)
resultant = sine1+sine2
resultant = .5+np.cos(ts*(peak_freqs[3]-peak_freqs[2])*2*np.pi-2)/2
fig = figure(width=700, height=300)
# fig.line(ts, sine1, color = 'blue')
# fig.line(ts, sine2, color = 'red')
fig.line(ts, resultant, color='purple')
fig.line(coupled_A.ts, less_decay_A/less_decay_A[coupled_A.ts<.0299].max())
fig.y_range = Range1d(-1.05, 1.05)

show(fig)

167.8 +- 0.1


In [203]:
omega_test = np.concatenate([omega_test_A, omega_test_B])
u = nu.print_unc(omega_test.mean(), omega_test.std())
omega_test

167.7 +- 0.2


array([167.65175362, 167.85339382, 167.46268424, 167.85339382])